In [1]:
from typing import Iterable
from limes_x.solver import Application, Endpoint, Transform, Namespace, Solve

NS = Namespace()
_ids = 0
_ids_map = {}
def make_node(name: str, ins: Iterable[str], outs:Iterable[str]) -> Transform:
    tr = Transform(NS)
    for x in ins:
        tr.AddRequirement([x])
    for x in outs:
        tr.AddProduct([x])
    return tr

def _test(name, transforms: list[Transform], given: set[str], targets:set[str], expected: list):
    print(f"{name}:")

    parsed_given: list[Endpoint] = []
    parsed_target = Transform(NS)
    for x in targets:
        parsed_target.AddRequirement(x)
    for x in given:
        parsed_given.append(Endpoint(NS, {x}))

    result = Solve(parsed_given, parsed_target, transforms)
    # if result is None or result == False: result = []

    def _print_sol(x: list[Application]):
        for a in x:
            print(a)

    failed = False
    if len(result.solution[:-1]) != len(expected):
        print(f"sol len diff")
        print(expected)
        _print_sol(result.solution)
        failed = True

    have = given
    for appl in result.solution:
        used = {e for g in [e.properties for e in appl.used] for e in g}
        if not used.issubset(have):
            print(f"transform missing requirements {appl}")
            _print_sol(result.solution)
            failed = True
            break

        have |= {e for g in [e.properties for e in appl.produced] for e in g}

    if not targets.issubset(have):
        print(f"failed to produce {targets - have}")
        failed = True
    
    if not failed: print(f"{name} solved in {result.steps} steps")
    else:
        print(result.message)
        _print_sol(result.solution)
    print()
    return result

In [2]:
r = _test(
    'complex',[
        make_node('sa', {'s'}, {'a', '_a'}),

        make_node('ab', {'a'}, {'b'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('ca', {'c'}, {'a'}),
        make_node('cx', {'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),

        make_node('_ab', {'_a'}, {'_b'}),
        make_node('_ay', {'_a'}, {'_y'}),
        make_node('_ac', {'_a'}, {'_c'}),
        make_node('_bc.x', {'_b', '_c'}, {'_x'}),
        make_node('_jx', {'_j'}, {'_x'}),

        make_node('+1', {'b', '_b'}, {'+1'}),
        make_node('+2', {'c', '_b', 'a'}, {'+2', 'a'}),
        make_node('+3', {'+1', '+2', '_y', '_c', 'c'}, {'j', '+3', 'x'}),

        make_node('end', {'+1', '+2', '+3'}, {'+x'})
    ],
    {'s'}, {'+x'},
    [
        make_node('sa', {'s'}, {'a', '_a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),

        make_node('_ab', {'_a'}, {'_b'}),
        make_node('_ac', {'_a'}, {'_c'}),
        make_node('_ay', {'_a'}, {'_y'}),

        make_node('+1', {'b', '_b'}, {'+1'}),
        make_node('+2', {'c', '_b', 'a'}, {'+2', 'a'}),
        make_node('+3', {'+1', '+2', '_y', '_c', 'c'}, {'+2', 'j', '+3', 'x'}),

        make_node('end', {'+1', '+2', '+3'}, {'+x'})
    ],
)
r

complex:
sol len diff
[<{s}->{a},{_a}>, <{a}->{b}>, <{b}->{c}>, <{_a}->{_b}>, <{_a}->{_c}>, <{_a}->{_y}>, <{_b},{b}->{+1}>, <{a},{c},{_b}->{a},{+2}>, <{_c},{+2},{c},{+1},{_y}->{+3},{+2},{j},{x}>, <{+3},{+1},{+2}->{+x}>]
failed to produce {'+x'}
step limit exceeded



Result(solution=[], message='step limit exceeded', evidence=deque([Solve.<locals>.State(have=[<136:s>, <137:a>, <138:_a>, <141:_b>, <156:_c>, <213:y>, <437:_y>, <1404:b>, <3780:c>, <6354:_x>, <9268:+1>], usage_signatures={1: {'!136'}, 30: {'!138'}, 38: {'!138'}, 10: {'!137'}, 34: {'!138'}, 6: {'!137'}, 14: {'!1404'}, 42: {'!156!141'}, 51: {'!141!1404'}}, plan=[Application(transform=<{s}->{a},{_a}>, used={<136:s>}, produced=[<137:a>, <138:_a>], signature='!136'), Application(transform=<{_a}->{_b}>, used={<138:_a>}, produced=[<141:_b>], signature='!138'), Application(transform=<{_a}->{_c}>, used={<138:_a>}, produced=[<156:_c>], signature='!138'), Application(transform=<{a}->{y}>, used={<137:a>}, produced=[<213:y>], signature='!137'), Application(transform=<{_a}->{_y}>, used={<138:_a>}, produced=[<437:_y>], signature='!138'), Application(transform=<{a}->{b}>, used={<137:a>}, produced=[<1404:b>], signature='!137'), Application(transform=<{b}->{c}>, used={<1404:b>}, produced=[<3780:c>], sig

In [3]:
todo = r.evidence
# s = todo.popleft()
for s in todo:
    # for a in s.plan:
    #     print(a)
    print(s.have)
    print()

Application(transform=<{s}->{a},{_a}>, used={<136:s>}, produced=[<137:a>, <138:_a>], signature='!136')
Application(transform=<{_a}->{_b}>, used={<138:_a>}, produced=[<141:_b>], signature='!138')
Application(transform=<{_a}->{_c}>, used={<138:_a>}, produced=[<156:_c>], signature='!138')
Application(transform=<{a}->{y}>, used={<137:a>}, produced=[<213:y>], signature='!137')
Application(transform=<{_a}->{_y}>, used={<138:_a>}, produced=[<437:_y>], signature='!138')
Application(transform=<{a}->{b}>, used={<137:a>}, produced=[<1404:b>], signature='!137')
Application(transform=<{b}->{c}>, used={<1404:b>}, produced=[<3780:c>], signature='!1404')
Application(transform=<{_c},{_b}->{_x}>, used={<156:_c>, <141:_b>}, produced=[<6354:_x>], signature='!156!141')
Application(transform=<{_b},{b}->{+1}>, used={<1404:b>, <141:_b>}, produced=[<9268:+1>], signature='!141!1404')

Application(transform=<{s}->{a},{_a}>, used={<136:s>}, produced=[<137:a>, <138:_a>], signature='!136')
Application(transform=<{_

In [ ]:
_test(
    'one',[
        make_node('ax', {'a'}, {'x'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('jx', {'j'}, {'x'}),
    ],
    {'a'}, {'x'},
    [
        make_node('ax', {'a'}, {'x'}),
    ],
)

_test(
    'line',[
        make_node('ab', {'a'}, {'b'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),
    ],
    {'a'}, {'x'},
    [
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
    ],
)

_test(
    'asymm diamond',[
        make_node('sss', {'s'}, {'ss'}),
        make_node('ssa', {'ss'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('ay', {'a'}, {'y'}),

        make_node('a_c', {'a'}, {'_c'}),
        # Node('bc.x', {'b', 'c'}, {'x'}),
        make_node('_cc.x', {'_c', 'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),
    ],
    {'s'}, {'x'},
    [
        make_node('sss', {'s'}, {'ss'}),
        make_node('ssa', {'ss'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('a_c', {'a'}, {'_c'}),
        make_node('_cc.x', {'_c', 'c'}, {'x'}),
    ],
)


_test(
    'loop',[
        make_node('ca', {'c'}, {'a'}),
        make_node('sa', {'s'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),
    ],
    {'s'}, {'x'},
    [
        make_node('sa', {'s'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
    ],
)

_test(
    'loop b',[
        make_node('sa', {'s'}, {'a'}),
        make_node('ca', {'c'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),
    ],
    {'s'}, {'x'},
    [
        make_node('sa', {'s'}, {'a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('cx', {'c'}, {'x'}),
    ],
)

_test(
    'loop vs fork',[
        make_node('sa', {'s'}, {'a'}),
        make_node('ab+', {'a'}, {'b', 'j', 'k'}),
        make_node('bk.c', {'b', 'k'}, {'c'}),
        make_node('c.x', {'c'}, {'x'}),
        make_node('ja', {'j'}, {'a'}),
    ],
    {'s'}, {'x'},
    [        
        make_node('sa', {'s'}, {'a'}),
        make_node('ab+', {'a'}, {'b', 'j', 'k'}),
        make_node('bk.c', {'b', 'k'}, {'c'}),
        make_node('c.x', {'c'}, {'x'}),
    ],
)

_test(
    'distributed',[
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c1'}),

        make_node('2', {'c1'}, {'c2'}),
        make_node('3', {'s1'}, {'c3'}),

        make_node('g', {'a', 'b', 'c1', 'c2', 'c3'}, {'g1', 'g2'}),

        make_node('*', {'c1', 'c2', 'c3', 's2', 'g1', 'g2'}, {'d'}),

        make_node('de', {'d'}, {'e'}),
        make_node('ex', {'e'}, {'x'})
    ],
    {'a', 's1', 's2'}, {'x'},
    [
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c1'}),

        make_node('2', {'c1'}, {'c2'}),
        make_node('3', {'s1'}, {'c3'}),
        
        make_node('g', {'a', 'b', 'c1', 'c2', 'c3'}, {'g1', 'g2'}),

        make_node('*', {'c1', 'c2', 'c3', 's2'}, {'d'}),

        make_node('de', {'d'}, {'e'}),
        make_node('ex', {'e'}, {'x'})
    ],
)

_test(
    'overlay',[
        make_node('s.abc', {'s'}, {'a', 'b', 'c'}),
        make_node('ab.jk', {'a', 'b'}, {'j', 'k'}),
        make_node('bc.ki', {'b', 'c'}, {'k', 'i'}),
        make_node('ca.ij', {'a', 'c'}, {'i', 'j'}),

        make_node('end', {'i', 'j', 'k'}, {'x'})
    ],
    {'s'}, {'x'},
    [
        make_node('s.abc', {'s'}, {'a', 'b', 'c'}),
        make_node('bc.ki', {'b', 'c'}, {'k', 'i'}),
        make_node('ca.ij', {'a', 'c'}, {'i', 'j'}),

        make_node('end', {'i', 'j', 'k'}, {'x'})
    ],
)

_test(
    'should pick shorter path',[
        make_node('s.ai', {'s'}, {'a', 'i'}),

        make_node('i.j', {'i'}, {'j'}),
        make_node('j.k', {'j'}, {'k'}),
        make_node('k.x', {'k'}, {'x'}),

        make_node('a.b', {'a'}, {'b'}),
        make_node('b.x', {'b'}, {'x'}),
    ],
    {"s"}, {"x"},
    [
        make_node('s.ai', {'s'}, {'a', 'i'}),
        make_node('a.b', {'a'}, {'b'}),
        make_node('b.x', {'b'}, {'x'}),
    ],
)

# {'+2'}
# {sa, ab, bc, _ab, _ay, _ac, +1, +3, end}
# {'j', '+1', '_y', 'b', 'x', 'c', '+x', '+3', 'a', '_a', '_c', '_b'}}
_test(
    'complex',[
        make_node('sa', {'s'}, {'a', '_a'}),

        make_node('ab', {'a'}, {'b'}),
        make_node('ay', {'a'}, {'y'}),
        make_node('bc', {'b'}, {'c'}),
        make_node('ca', {'c'}, {'a'}),
        make_node('cx', {'c'}, {'x'}),
        make_node('jx', {'j'}, {'x'}),

        make_node('_ab', {'_a'}, {'_b'}),
        make_node('_ay', {'_a'}, {'_y'}),
        make_node('_ac', {'_a'}, {'_c'}),
        make_node('_bc.x', {'_b', '_c'}, {'_x'}),
        make_node('_jx', {'_j'}, {'_x'}),

        make_node('+1', {'b', '_b'}, {'+1'}),
        make_node('+2', {'c', '_b', 'a'}, {'+2', 'a'}),
        make_node('+3', {'+1', '+2', '_y', '_c', 'c'}, {'j', '+3', 'x'}),

        make_node('end', {'+1', '+2', '+3'}, {'+x'})
    ],
    {'s'}, {'+x'},
    [
        make_node('sa', {'s'}, {'a', '_a'}),
        make_node('ab', {'a'}, {'b'}),
        make_node('bc', {'b'}, {'c'}),

        make_node('_ab', {'_a'}, {'_b'}),
        make_node('_ac', {'_a'}, {'_c'}),
        make_node('_ay', {'_a'}, {'_y'}),

        make_node('+1', {'b', '_b'}, {'+1'}),
        make_node('+2', {'c', '_b', 'a'}, {'+2', 'a'}),
        make_node('+3', {'+1', '+2', '_y', '_c', 'c'}, {'+2', 'j', '+3', 'x'}),

        make_node('end', {'+1', '+2', '+3'}, {'+x'})
    ],
)